In [0]:
%pip install requests

In [0]:
dbutils.library.restartPython()

In [0]:
dbutils.fs.ls("/mnt/processed")

In [0]:
import pandas as pd

# Ensure the file path includes the correct extension, such as '.csv'
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_general.csv")
display(df)

### **expandir la columna {actions} crear columnas de cada seccion para su analisis**

In [0]:
#expandir a detalle columna actions y guardarla
import pandas as pd
import json

#cargar el csv guardado
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_general.csv")

#Funcion para expandir columna actions
def expand_actions(actions):
    try:
        actions_list = json.loads(actions.replace("'", "\""))
        expanded = {action['action_type']: action['value'] for action in actions_list}
        return pd.Series(expanded)
    except Exception as e:
        print(f"Error al procesar la fila: {e}")
        return pd.Series()
    
#se aplica la funcion a la columna 'actions' y concatena los resultados
df_expanded = df['actions'].apply(expand_actions)

#concatenar las columnas nuevas con el Dataframe original
df_final = pd.concat([df.drop('actions', axis=1), df_expanded], axis=1)

#guardar el resultado en el CSV
df_final.to_csv("/dbfs/mnt/processed/anuncios_insights_general_expanded.csv", index=False)
print(df_final.columns)

#Revisar cambios
display(df_final)
print(df.columns)

## **Convertir a formato correcto de hora, extraer solo la hora de inicio para tomarlo como referencia**

In [0]:
import pandas as pd

# Leer el archivo CSV
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_general_expanded.csv")

# Extraer la hora de inicio de cada intervalo (la primera parte del rango)
df['hora_inicio'] = df['hourly_stats_aggregated_by_advertiser_time_zone'].str.split(' - ').str[0]

#convertir la hora_inicio al formato string para evitar problemas al guardar
df['hora_inicio'] =df['hora_inicio'].astype(str)

# Guardar el dataframe modificado en un nuevo archivo CSV
df.to_csv("/dbfs/mnt/processed/anuncios_insights_general_hora_inicio.csv", index=False)

print("CSV modificado y guardado exitosamente.")
display(df)


## **Borrar columna hourly_stats_aggregated_by_advertiser_time_zone
## ya que se extrajo lo necesario**

In [0]:
import pandas as pd

#leer el archivo desde la ruta especificada
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_general_hora_inicio.csv")

#ELIMINAR LA COLUMNA QUE NO SE OCUPA
df= df.drop(columns=['hourly_stats_aggregated_by_advertiser_time_zone'])

#Guardar el dataframe modificado en un nuevo archivo CSV
df.to_csv("/dbfs/mnt/processed/anuncios_insights_general_hora_inicio_clean.csv", index=False)
print("CSV modificado y guardado exitosamente.")

## Cambiar a tipo numerico todos los parametros **necesarios**

In [0]:
import pandas as pd

df =pd.read_csv("/dbfs/mnt/processed/anuncios_insights_general_hora_inicio_clean.csv")
#Convertir columnas a tipo numero

columns_to_convert=['onsite_conversion.messaging_user_depth_2_message_send',
       'onsite_conversion.messaging_conversation_started_7d', 'video_view',
       'post_reaction', 'link_click', 'post', 'onsite_conversion.post_save',
       'comment', 'onsite_conversion.messaging_user_depth_3_message_send',
       'like', 'onsite_conversion.messaging_welcome_message_view',
       'onsite_conversion.messaging_conversation_replied_7d',
       'onsite_conversion.messaging_user_depth_5_message_send']
#convertir cada columna a tipo numerico
for column in columns_to_convert:
    if column in df.columns:
        df[column] = pd.to_numeric(df[column], errors='coerce')
    else:
        print(f"Column {column} does not exist in DataFrame.")

#guardar el csv modificado
df.to_csv("/dbfs/mnt/processed/anuncios_insights_gral_convertidos.csv", index=False)

#mostrar cambio
display(df)

ad_id ad_name adset_name campaign_name date_start date_stop impressions spend clicks inline_link_clicks cpc cpm buying_type onsite_conversion.total_messaging_connection onsite_conversion.messaging_first_reply post_engagement page_engagement onsite_conversion.messaging_welcome_message_view onsite_conversion.messaging_conversation_started_7d post_reaction link_click like onsite_conversion.messaging_conversation_replied_7d video_view comment onsite_conversion.messaging_user_depth_2_message_send onsite_conversion.messaging_user_depth_3_message_send post onsite_conversion.post_save onsite_conversion.messaging_user_depth_5_message_send hora_inicio 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1261.0 37.541805 39.0 12.0 0.96261 29.771455 AUCTION 1.0 1.0 13.0 13.0 2.0 1.0 1.0 12.0 null null null null null null null null null 19:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1040.0 35.482803 36.0 5.0 0.985633 34.11808 AUCTION null null 5.0 6.0 2.0 null null 5.0 1.0 null null null null null null null null 20:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 942.0 33.553738 30.0 3.0 1.118458 35.619679 AUCTION 2.0 2.0 3.0 3.0 3.0 2.0 null 3.0 null 2.0 null null null null null null null 21:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 497.0 18.790893 16.0 2.0 1.174431 37.808637 AUCTION null null 2.0 2.0 null null null 2.0 null null null null null null null null null 22:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 655.0 19.060762 12.0 3.0 1.588397 29.1004 AUCTION null null 3.0 3.0 null null null 3.0 null null null null null null null null null 23:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 5.0 0.451567 2.0 1.0 0.225784 90.313461 AUCTION null null 3.0 3.0 null null null 1.0 null null 2.0 null null null null null null 00:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 10.0 0.379727 0.0 null null 37.972705 AUCTION null null 3.0 3.0 null null null null null null 3.0 null null null null null null 01:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 4.0 0.205258 2.0 null 0.102629 51.314466 AUCTION null null 1.0 1.0 null null null null null null 1.0 null null null null null null 02:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 6.0 0.626036 0.0 null null 104.339415 AUCTION null null 1.0 1.0 null null null null null null 1.0 null null null null null null 03:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 9.0 0.31815 2.0 null 0.159075 35.349966 AUCTION null null 2.0 2.0 null null null null null null 1.0 1.0 null null null null null 06:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 15.0 1.980738 1.0 null 1.980738 132.049227 AUCTION null null 6.0 6.0 null null null null null null 6.0 null null null null null null 07:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 40.0 4.023054 1.0 null 4.023054 100.576354 AUCTION null null 12.0 12.0 null null null null null null 12.0 null null null null null null 08:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024

## **cambiar columnas del english al spanish**

In [0]:
#cambiar columnas de csv con mas detalles en spanish
import pandas as pd

#leer el csv desde la ruta especificada
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_gral_convertidos.csv")

#diccionario con los cambios de nombres en columnas/agregar nombres columnas a cambiar por nuevos nombres
new_column_names ={
    'ad_id': 'id_anuncio',
    'ad_name': 'nombre_anuncio',
    'campaign_name': 'nombre_campana',
    'date_start': 'fecha_inicio',
    'date_stop': 'fecha_finalizacion',
    'reach': 'personas_alcanzadas',
    'impressions': 'veces_mostrado',
    'frequency': 'promedio_frecuencia',
    'spend': 'gasto',
    'clicks': 'clicks_en_anuncio',
    'inline_link_clicks': 'click_enlace_trafico',
    'conversion_rate_ranking': 'conversion_mercado',
    'cpc': 'costo_por_click_anuncio',
    'cpp': 'costo_por_resultado',
    'cpm': 'costo_por_mil_impresiones',
    'quality_ranking': 'calidad_mercado',
    'buying_type': 'tipo_compra',
    'onsite_conversion.total_messaging_connection': 'conversion_boton_msj',
    'onsite_conversion.messaging_first_reply': 'conversion_primer_respuesta',
    'post_engagement': 'interaccion_post',
    'page_engagement': 'interaccion_page',
    'onsite_conversion.messaging_user_depth_2_message_send': '2do_msj_cliente',
    'onsite_conversion.messaging_conversation_started_7d': 'msj_iniciado_7Dias',
    'video_view': 'vistas_video',
    'post_reaction': 'reacciones_post',
    'link_click': 'click_link',
    'post': 'contenido_publicado',
    'onsite_conversion.post_save': 'contenido_guardado',
    'comment': 'comentarios',
    'onsite_conversion.messaging_user_depth_3_message_send': '3er_msj_cliente',
    'like': 'like',
    'onsite_conversion.messaging_welcome_message_view': 'vistas_mensaje_bienvenida',
    'onsite_conversion.messaging_conversation_replied_7d': 'msjs_respondidos_en_7Dias',
    'onsite_conversion.messaging_user_depth_5_message_send': '5to_msj_cliente'
    # Agrega todos los nombres de columnas que deseas cambiar
    
}

# Renombrar las columnas
df.rename(columns=new_column_names, inplace=True)

# Guardar el DataFrame renombrado en un nuevo archivo CSV
df.to_csv("/dbfs/mnt/processed/anuncios_insights_gral_rename.csv", index=False)

print("Archivo renombrado y guardado exitosamente.")
display(df)

Archivo renombrado y guardado exitosamente.


id_anuncio nombre_anuncio adset_name nombre_campana fecha_inicio fecha_finalizacion veces_mostrado gasto clicks_en_anuncio click_enlace_trafico costo_por_click_anuncio costo_por_mil_impresiones tipo_compra conversion_boton_msj conversion_primer_respuesta interaccion_post interaccion_page vistas_mensaje_bienvenida msj_iniciado_7Dias reacciones_post click_link like msjs_respondidos_en_7Dias vistas_video comentarios 2do_msj_cliente 3er_msj_cliente contenido_publicado contenido_guardado 5to_msj_cliente hora_inicio 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1261.0 37.541805 39.0 12.0 0.96261 29.771455 AUCTION 1.0 1.0 13.0 13.0 2.0 1.0 1.0 12.0 null null null null null null null null null 19:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1040.0 35.482803 36.0 5.0 0.985633 34.11808 AUCTION null null 5.0 6.0 2.0 null null 5.0 1.0 null null null null null null null null 20:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 942.0 33.553738 30.0 3.0 1.118458 35.619679 AUCTION 2.0 2.0 3.0 3.0 3.0 2.0 null 3.0 null 2.0 null null null null null null null 21:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 497.0 18.790893 16.0 2.0 1.174431 37.808637 AUCTION null null 2.0 2.0 null null null 2.0 null null null null null null null null null 22:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 655.0 19.060762 12.0 3.0 1.588397 29.1004 AUCTION null null 3.0 3.0 null null null 3.0 null null null null null null null null null 23:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 5.0 0.451567 2.0 1.0 0.225784 90.313461 AUCTION null null 3.0 3.0 null null null 1.0 null null 2.0 null null null null null null 00:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 10.0 0.379727 0.0 null null 37.972705 AUCTION null null 3.0 3.0 null null null null null null 3.0 null null null null null null 01:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 4.0 0.205258 2.0 null 0.102629 51.314466 AUCTION null null 1.0 1.0 null null null null null null 1.0 null null null null null null 02:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 6.0 0.626036 0.0 null null 104.339415 AUCTION null null 1.0 1.0 null null null null null null 1.0 null null null null null null 03:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 9.0 0.31815 2.0 null 0.159075 35.349966 AUCTION null null 2.0 2.0 null null null null null null 1.0 1.0 null null null null null 06:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 15.0 1.980738 1.0 null 1.980738 132.049227 AUCTION null null 6.0 6.0 null null null null null null 6.0 null null null null null null 07:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 40.0 4.023054 1.0 null 4.023054 100.576354 AUCTION null null 12.0 12.0 null null null null null null 12.0 null null null null null null 08:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 46.0 3.520172 2.0 null 1.760086 76.525487 AUCTION null null 11.0 11.0 null null null null null null 11.0 null null n

## **Cambiar el idioma de las columnas de english a spanish**

In [0]:
#cambiar el contenido de las columnas de spanish a english
import pandas as pd

#cargar el archivo csv de origen en un dataframe
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_gral_rename.csv")

#listar las columnas que vamos a remplazar
columns_to_replace=['tipo_compra']

#diccionario con los valores a remplazar y los nuevos valores
replacements = {
    'UNKNOWN': 'desconocido',
    'ABOVE_AVERAGE': 'arriba del promedio',
    'AVERAGE': 'promedio',
    'BELOW_AVERAGE_35': 'abajo del promedio',
    'BELOW_AVERAGE_20': 'abajo del promedio',
    'AUCTION':'subasta'

}

#remplazamos valores 'UNKNOWN' por 'desconocido'
df[columns_to_replace]=df[columns_to_replace].replace(replacements)

#guardar el dataframe en un nuevo archivo csv
df.to_csv("/dbfs/mnt/processed/anuncios_insights_general_limpio.csv", index=False)
print("Archivo renombrado y guardado exitosamente.")
display(df)

Archivo renombrado y guardado exitosamente.


id_anuncio nombre_anuncio adset_name nombre_campana fecha_inicio fecha_finalizacion veces_mostrado gasto clicks_en_anuncio click_enlace_trafico costo_por_click_anuncio costo_por_mil_impresiones tipo_compra conversion_boton_msj conversion_primer_respuesta interaccion_post interaccion_page vistas_mensaje_bienvenida msj_iniciado_7Dias reacciones_post click_link like msjs_respondidos_en_7Dias vistas_video comentarios 2do_msj_cliente 3er_msj_cliente contenido_publicado contenido_guardado 5to_msj_cliente hora_inicio 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1261.0 37.541805 39.0 12.0 0.96261 29.771455 subasta 1.0 1.0 13.0 13.0 2.0 1.0 1.0 12.0 null null null null null null null null null 19:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 1040.0 35.482803 36.0 5.0 0.985633 34.11808 subasta null null 5.0 6.0 2.0 null null 5.0 1.0 null null null null null null null null 20:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 942.0 33.553738 30.0 3.0 1.118458 35.619679 subasta 2.0 2.0 3.0 3.0 3.0 2.0 null 3.0 null 2.0 null null null null null null null 21:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 497.0 18.790893 16.0 2.0 1.174431 37.808637 subasta null null 2.0 2.0 null null null 2.0 null null null null null null null null null 22:00:00 120209973174170669 Test_Ad_Trend_CasaFamosos Test_Group_Trends_Express Test_Camp_Trends_Express 2024-08-11 2024-09-09 655.0 19.060762 12.0 3.0 1.588397 29.1004 subasta null null 3.0 3.0 null null null 3.0 null null null null null null null null null 23:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 5.0 0.451567 2.0 1.0 0.225784 90.313461 subasta null null 3.0 3.0 null null null 1.0 null null 2.0 null null null null null null 00:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 10.0 0.379727 0.0 null null 37.972705 subasta null null 3.0 3.0 null null null null null null 3.0 null null null null null null 01:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 4.0 0.205258 2.0 null 0.102629 51.314466 subasta null null 1.0 1.0 null null null null null null 1.0 null null null null null null 02:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 6.0 0.626036 0.0 null null 104.339415 subasta null null 1.0 1.0 null null null null null null 1.0 null null null null null null 03:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 9.0 0.31815 2.0 null 0.159075 35.349966 subasta null null 2.0 2.0 null null null null null null 1.0 1.0 null null null null null 06:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 15.0 1.980738 1.0 null 1.980738 132.049227 subasta null null 6.0 6.0 null null null null null null 6.0 null null null null null null 07:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 40.0 4.023054 1.0 null 4.023054 100.576354 subasta null null 12.0 12.0 null null null null null null 12.0 null null null null null null 08:00:00 120209780494910669 Test_Ad_Ultimas5-t82Morillo Test_ConjuntoMorillo_Ultimas_t82 Test_Gen_Wha_Morillo_Ago24_Campaña 2024-08-11 2024-09-09 46.0 3.520172 2.0 null 1.760086 76.525487 subasta null null 11.0 11.0 null null null null null null 11.0 null null n

In [0]:
df = pd.read_csv("/dbfs/mnt/processed/anuncios_insights_clean05_09_2024.csv")
display(df)